In [1]:
import gymnasium
import push_box
import pybullet as p
import pybullet_data
import time
from stable_baselines3 import PPO
from stable_baselines3.common.vec_env import DummyVecEnv
from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.common.callbacks import EvalCallback, StopTrainingOnRewardThreshold
import os
from typing import Any, Dict
import torch as th

pybullet build time: Nov 28 2023 23:48:36
2024-03-08 15:58:35.926043: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-03-08 15:58:35.926072: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-03-08 15:58:35.927079: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-03-08 15:58:35.932813: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
202

In [4]:
p.disconnect()

numActiveThreads = 0
stopping threads
Thread with taskId 0 exiting
Thread TERMINATED
destroy semaphore
semaphore destroyed
destroy main semaphore
main semaphore destroyed
finished
numActiveThreads = 0
btShutDownExampleBrowser stopping threads
Thread with taskId 0 exiting
Thread TERMINATED
destroy semaphore
semaphore destroyed
destroy main semaphore
main semaphore destroyed


In [2]:
log_path = os.path.join('Training', 'Logs')

In [3]:
env = gymnasium.make('pushBox-v0')
env = DummyVecEnv([lambda: env])

In [4]:
# Add a callback to training stage for early stopping
save_path = os.path.join('Training', 'SavedModels', 'PPO_87_best')
stop_callback = StopTrainingOnRewardThreshold(reward_threshold = 100, verbose = 1)
eval_callback = EvalCallback(env, 
                            callback_on_new_best = stop_callback,
                            eval_freq = 10000, 
                            best_model_save_path = save_path, 
                            verbose = 1)


In [5]:
# Learning rate schedule: linearly decreasing from 0.0007 to 0.0001
def linear_lr(progress_remaining: float):
    start_lr = 0.00005
    end_lr = 0.0002
    return end_lr + (start_lr - end_lr) * progress_remaining

In [6]:
model = PPO('MlpPolicy', env, learning_rate=linear_lr, verbose=1, tensorboard_log=log_path)

Using cuda device


In [7]:
model.learn(total_timesteps=10000000, callback=eval_callback)

Logging to Training/Logs/PPO_87
-----------------------------
| time/              |      |
|    fps             | 835  |
|    iterations      | 1    |
|    time_elapsed    | 2    |
|    total_timesteps | 2048 |
-----------------------------
------------------------------------------
| time/                   |              |
|    fps                  | 548          |
|    iterations           | 2            |
|    time_elapsed         | 7            |
|    total_timesteps      | 4096         |
| train/                  |              |
|    approx_kl            | 0.0009933448 |
|    clip_fraction        | 9.77e-05     |
|    clip_range           | 0.2          |
|    entropy_loss         | -2.84        |
|    explained_variance   | 0.874        |
|    learning_rate        | 3e-05        |
|    loss                 | 0.00327      |
|    n_updates            | 10           |
|    policy_gradient_loss | -0.00111     |
|    std                  | 0.998        |
|    value_loss           |

/home/danielmasamba/anaconda3/envs/dan/lib/python3.11/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Eval num_timesteps=10000, episode_reward=-1.00 +/- 0.00
Episode length: 300.00 +/- 0.00
-----------------------------------------
| eval/                   |             |
|    mean_ep_length       | 300         |
|    mean_reward          | -1          |
| time/                   |             |
|    total_timesteps      | 10000       |
| train/                  |             |
|    approx_kl            | 0.001204306 |
|    clip_fraction        | 4.88e-05    |
|    clip_range           | 0.2         |
|    entropy_loss         | -2.83       |
|    explained_variance   | 0.891       |
|    learning_rate        | 3.01e-05    |
|    loss                 | -0.00115    |
|    n_updates            | 40          |
|    policy_gradient_loss | -0.000952   |
|    std                  | 0.998       |
|    value_loss           | 0.00489     |
-----------------------------------------
New best mean reward!
------------------------------
| time/              |       |
|    fps             | 464   |

In [10]:
PPO_Path = os.path.join('Training', 'SavedModels', 'PPO_87_10M_15_degree_cylinder')

In [11]:
model.save(PPO_Path)

In [12]:
del model

In [13]:
model = PPO.load(PPO_Path, env=env)

In [16]:
evaluate_policy(model, env, n_eval_episodes=10)

box reached target
box reached target
box reached target
box reached target
box reached target
box reached target
box reached target


(3.5598271869488145, 2.772078309024191)

In [16]:
p.disconnect()

error: Not connected to physics server.